In [1]:
import os
import cv2
import json
import numpy as np
from ultralytics import YOLO
from tqdm import tqdm  # 진행 상태 표시 라이브러리

# YOLO Pose 모델 로드
model = YOLO("yolov8n-pose.pt")  # YOLOv8 Pose 모델 경로

# 최상위 폴더 경로
base_dir = "/home/hyun/dev_ws/ROS_project/pose/Validation"  # 최상위 폴더 경로

# NumPy 데이터를 Python 데이터로 변환하는 함수
def numpy_to_python(obj):
    if isinstance(obj, (np.integer, np.int64, np.int32)):
        return int(obj)
    elif isinstance(obj, (np.floating, np.float64, np.float32)):
        return float(obj)
    elif isinstance(obj, np.ndarray):
        return obj.tolist()
    raise TypeError(f"Object of type {obj.__class__.__name__} is not JSON serializable")

# 랜드마크 정규화 함수
def normalize_landmarks(landmarks, image_width, image_height):
    landmarks[:, 0] /= image_width  # x 좌표 정규화
    landmarks[:, 1] /= image_height  # y 좌표 정규화
    return landmarks

# 랜드마크 추출 함수
def extract_landmarks(image_path):
    """
    YOLO Pose로 랜드마크를 추출하고 정규화합니다.
    Args:
        image_path (str): 이미지 경로
    Returns:
        List[Dict]: 탐지된 모든 사람의 랜드마크 데이터 리스트
    """
    image = cv2.imread(image_path)
    if image is None:
        print(f"Error: Unable to load image at {image_path}")
        return []

    image_height, image_width = image.shape[:2]  # 이미지 크기
    results = model(image)
    people_landmarks = []

    # YOLO 결과 확인
    if len(results) == 0 or not hasattr(results[0], 'keypoints'):
        print(f"No keypoints detected for {image_path}")
        return []

    keypoints = results[0].keypoints.xy.cpu().numpy()  # (N, 17, 2)
    confidence = results[0].keypoints.conf.cpu().numpy()  # (N, 17)

    for person_id, (kp, conf) in enumerate(zip(keypoints, confidence), start=1):
        # (17, 3) 형태로 결합하고 정규화
        landmarks = np.concatenate([kp, conf[:, None]], axis=1)
        normalized_landmarks = normalize_landmarks(landmarks, image_width, image_height)
        people_landmarks.append({
            "person_id": person_id,
            "landmarks": normalized_landmarks.flatten().tolist()  # 리스트로 변환
        })

    return people_landmarks

# 재귀적으로 하위 폴더 순회 및 이미지 처리
def process_folder(folder_path, class_name):
    """
    주어진 폴더의 이미지를 처리하여 JSON 파일로 저장합니다.
    Args:
        folder_path (str): 현재 폴더 경로
        class_name (str): 클래스 이름 (lying, running 등)
    """
    for root, dirs, files in os.walk(folder_path):  # 하위 폴더까지 모두 순회
        dirs.sort()  # 하위 폴더를 정렬
        files.sort()  # 파일을 정렬

        for subfolder in dirs:
            subfolder_path = os.path.join(root, subfolder)
            sequence_data = {"class_name": class_name, "sequence": []}

            # 하위 서브폴더 내 이미지 처리
            images = [f for f in os.listdir(subfolder_path) if f.lower().endswith(('.png', '.jpg', '.jpeg'))]
            images.sort()  # 파일 이름 정렬
            for idx, image in enumerate(tqdm(images, desc=f"Processing {subfolder_path}")):
                image_path = os.path.join(subfolder_path, image)
                people_landmarks = extract_landmarks(image_path)
                if people_landmarks:  # 랜드마크가 있으면 추가
                    sequence_data["sequence"].append({
                        "frame": idx + 1,
                        "people": people_landmarks
                    })

            # JSON 파일 저장
            output_path = os.path.join(subfolder_path, f"{os.path.basename(subfolder_path)}_output.json")
            with open(output_path, "w") as json_file:
                json.dump(sequence_data, json_file, indent=4, default=numpy_to_python)
            print(f"Saved JSON to: {output_path}")

# 최상위 폴더 순회
for class_name in tqdm(os.listdir(base_dir), desc="Processing Classes"):
    class_path = os.path.join(base_dir, class_name)
    if not os.path.isdir(class_path):
        continue  # 폴더가 아니면 건너뜀

    print(f"Processing class: {class_name}")
    process_folder(class_path, class_name)


Processing Classes:   0%|          | 0/4 [00:00<?, ?it/s]

Processing class: running


Processing /home/hyun/dev_ws/ROS_project/pose/Validation/running/0018_M217M218: 0it [00:00, ?it/s]


Saved JSON to: /home/hyun/dev_ws/ROS_project/pose/Validation/running/0018_M217M218/0018_M217M218_output.json


Processing /home/hyun/dev_ws/ROS_project/pose/Validation/running/0018_M219M220: 0it [00:00, ?it/s]


...


0: 384x640 2 persons, 6.2ms
Speed: 2.5ms preprocess, 6.2ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 6.3ms
Speed: 1.9ms preprocess, 6.3ms inference, 1.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 7.0ms
Speed: 1.8ms preprocess, 7.0ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 5.4ms
Speed: 1.5ms preprocess, 5.4ms inference, 1.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 6.3ms
Speed: 1.9ms preprocess, 6.3ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 6.3ms
Speed: 1.9ms preprocess, 6.3ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)



0: 384x640 2 persons, 5.6ms
Speed: 1.8ms preprocess, 5.6ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 5.7ms
Speed: 1.5ms preprocess, 5.7ms inference, 1.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 5.7ms
Speed: 2.0ms preprocess, 5.7ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 6.5ms
Speed: 2.1ms preprocess, 6.5ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 7.7ms
Speed: 2.4ms preprocess, 7.7ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 6.8ms
Speed: 2.1ms preprocess, 6.8ms inference, 1.9ms postprocess per image at shape (1, 3, 384, 640)


Processing /home/hyun/dev_ws/ROS_project/pose/Validation/sitting/0149_M532M533/0149_M532M533_R_B_17546_18060: 100%|██████████| 104/104 [00:02<00:00, 46.48it/s]
Processing Classes: 100%|██████████| 4/4 [08:59<00:00, 144.53s/it]

Saved JSON to: /home/hyun/dev_ws/ROS_project/pose/Validation/sitting/0149_M532M533/0149_M532M533_R_B_17546_18060/0149_M532M533_R_B_17546_18060_output.json


Processing Classes: 100%|██████████| 4/4 [08:59<00:00, 134.93s/it]


In [2]:
import numpy as np
import json
import os

def load_json_data(json_path, target_frames=96, num_landmarks=17):
    """
    JSON 파일에서 첫 번째 사람의 랜드마크 좌표를 로드하고, 
    연속성을 유지하면서 사람이 없는 프레임 처리
    """
    with open(json_path, "r") as file:
        data = json.load(file)
    
    sequence = []
    last_valid_landmarks = None
    
    for frame_data in data.get("sequence", []):
        people = frame_data.get("people", [])
        if people:
            # 첫 번째 사람의 랜드마크 사용
            landmarks = np.array(people[0]["landmarks"]).reshape(num_landmarks, 3)[:, :2]
            sequence.append(landmarks)
            last_valid_landmarks = landmarks
        elif last_valid_landmarks is not None:
            # 마지막으로 감지된 랜드마크 사용
            sequence.append(last_valid_landmarks)
    
    # 시퀀스 길이 조정
    if len(sequence) > target_frames:
        sequence = sequence[:target_frames]
    elif len(sequence) < target_frames:
        padding = [sequence[-1]] * (target_frames - len(sequence))
        sequence.extend(padding)
    
    return np.array(sequence)


# JSON 데이터 경로
json_dir = "/home/hyun/dev_ws/ROS_project/pose/Training"

# 데이터 로드
X_data = []
y_labels = []
for class_name in os.listdir(json_dir):
    class_path = os.path.join(json_dir, class_name)
    if os.path.isdir(class_path):
        for subfolder in os.listdir(class_path):
            subfolder_path = os.path.join(class_path, subfolder)
            if os.path.isdir(subfolder_path):
                for video_folder in os.listdir(subfolder_path):
                    video_path = os.path.join(subfolder_path, video_folder)
                    json_file = os.path.join(video_path, f"{video_folder}_output.json")
                    
                    if os.path.exists(json_file):
                        # 첫 번째 사람의 시퀀스만 로드
                        sequence = load_json_data(json_file, target_frames=96)
                        X_data.append(sequence)
                        y_labels.append(class_name)

# Numpy 배열로 변환
X_data = np.array(X_data)
y_labels = np.array(y_labels)

# 결과 출력
print(f"X_data shape: {X_data.shape}")
print(f"y_labels shape: {y_labels.shape}")

X_data shape: (1110, 96, 17, 2)
y_labels shape: (1110,)


In [23]:
import numpy as np
import json
import os

def load_json_data(json_path, target_frames=96, num_landmarks=17, max_people=3):
    """
    JSON 파일에서 여러 사람의 독립 시퀀스 생성
    """
    with open(json_path, "r") as file:
        data = json.load(file)
    
    all_sequences = []
    for person_idx in range(max_people):
        sequence = []
        last_valid_landmarks = None
        
        for frame_data in data.get("sequence", []):
            people = frame_data.get("people", [])
            
            if len(people) > person_idx:
                # 해당 인덱스의 사람 랜드마크 사용
                landmarks = np.array(people[person_idx]["landmarks"]).reshape(num_landmarks, 3)[:, :2]
                sequence.append(landmarks)
                last_valid_landmarks = landmarks
            elif last_valid_landmarks is not None:
                # 마지막으로 감지된 랜드마크 사용
                sequence.append(last_valid_landmarks)
        
        # 시퀀스 길이 조정
        if len(sequence) > 0:  # 유효한 시퀀스만 추가
            if len(sequence) > target_frames:
                sequence = sequence[:target_frames]
            elif len(sequence) < target_frames:
                padding = [sequence[-1]] * (target_frames - len(sequence))
                sequence.extend(padding)
            
            all_sequences.append(np.array(sequence))
    
    return all_sequences


# JSON 데이터 경로
json_dir = "/home/hyun/dev_ws/ROS_project/pose/Training"

# 데이터 로드
X_data = []
y_labels = []
for class_name in os.listdir(json_dir):
    class_path = os.path.join(json_dir, class_name)
    if os.path.isdir(class_path):
        for subfolder in os.listdir(class_path):
            subfolder_path = os.path.join(class_path, subfolder)
            if os.path.isdir(subfolder_path):
                for video_folder in os.listdir(subfolder_path):
                    video_path = os.path.join(subfolder_path, video_folder)
                    json_file = os.path.join(video_path, f"{video_folder}_output.json")
                    
                    if os.path.exists(json_file):
                        # 여러 사람의 독립 시퀀스 로드
                        sequences = load_json_data(json_file, target_frames=96)
                        
                        # 각 시퀀스에 대해 데이터 추가
                        for sequence in sequences:
                            X_data.append(sequence)
                            y_labels.append(class_name)

# Numpy 배열로 변환
train_X_data = np.array(X_data)
train_y_labels = np.array(y_labels)

# 결과 출력
print(f"train_X_data shape: {train_X_data.shape}")
print(f"train_y_labels shape: {train_y_labels.shape}")

train_X_data shape: (2918, 96, 17, 2)
train_y_labels shape: (2918,)


In [24]:
import numpy as np
import json
import os

def load_json_data(json_path, target_frames=96, num_landmarks=17, max_people=3):
    """
    JSON 파일에서 여러 사람의 독립 시퀀스 생성
    """
    with open(json_path, "r") as file:
        data = json.load(file)
    
    all_sequences = []
    for person_idx in range(max_people):
        sequence = []
        last_valid_landmarks = None
        
        for frame_data in data.get("sequence", []):
            people = frame_data.get("people", [])
            
            if len(people) > person_idx:
                # 해당 인덱스의 사람 랜드마크 사용
                landmarks = np.array(people[person_idx]["landmarks"]).reshape(num_landmarks, 3)[:, :2]
                sequence.append(landmarks)
                last_valid_landmarks = landmarks
            elif last_valid_landmarks is not None:
                # 마지막으로 감지된 랜드마크 사용
                sequence.append(last_valid_landmarks)
        
        # 시퀀스 길이 조정
        if len(sequence) > 0:  # 유효한 시퀀스만 추가
            if len(sequence) > target_frames:
                sequence = sequence[:target_frames]
            elif len(sequence) < target_frames:
                padding = [sequence[-1]] * (target_frames - len(sequence))
                sequence.extend(padding)
            
            all_sequences.append(np.array(sequence))
    
    return all_sequences


# JSON 데이터 경로
json_dir = "/home/hyun/dev_ws/ROS_project/pose/Validation"

# 데이터 로드
X_data = []
y_labels = []
for class_name in os.listdir(json_dir):
    class_path = os.path.join(json_dir, class_name)
    if os.path.isdir(class_path):
        for subfolder in os.listdir(class_path):
            subfolder_path = os.path.join(class_path, subfolder)
            if os.path.isdir(subfolder_path):
                for video_folder in os.listdir(subfolder_path):
                    video_path = os.path.join(subfolder_path, video_folder)
                    json_file = os.path.join(video_path, f"{video_folder}_output.json")
                    
                    if os.path.exists(json_file):
                        # 여러 사람의 독립 시퀀스 로드
                        sequences = load_json_data(json_file, target_frames=96)
                        
                        # 각 시퀀스에 대해 데이터 추가
                        for sequence in sequences:
                            X_data.append(sequence)
                            y_labels.append(class_name)

# Numpy 배열로 변환
val_X_data = np.array(X_data)
val_y_labels = np.array(y_labels)

# 결과 출력
print(f"val_X_data shape: {val_X_data.shape}")
print(f"val_y_labels shape: {val_y_labels.shape}")

val_X_data shape: (596, 96, 17, 2)
val_y_labels shape: (596,)


In [25]:
import torch
from torch.utils.data import DataLoader, Dataset, random_split
import torch.nn as nn

# 클래스 이름을 정수로 변환
class_names = sorted(set(train_y_labels))
class_to_idx = {name: idx for idx, name in enumerate(class_names)}
train_y_labels = np.array([class_to_idx[label] for label in train_y_labels])  # 문자열을 정수로 변환
class_names = sorted(set(val_y_labels))
class_to_idx = {name: idx for idx, name in enumerate(class_names)}
val_y_labels = np.array([class_to_idx[label] for label in val_y_labels])  # 문자열을 정수로 변환

# PyTorch Dataset 정의
class PoseDataset(Dataset):
    def __init__(self, X, y):
        self.X = torch.tensor(X, dtype=torch.float32)  # 입력 데이터
        self.y = torch.tensor(y, dtype=torch.long)  # 정수 레이블

    def __len__(self):
        return len(self.X)

    def __getitem__(self, idx):
        return self.X[idx], self.y[idx]


# 데이터 준비
train_dataset = PoseDataset(train_X_data, train_y_labels)
val_dataset = PoseDataset(val_X_data, val_y_labels)

# DataLoader 생성
batch_size = 32
train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=batch_size)

# 결과 확인
print(f"Train dataset size: {len(train_dataset)}")
print(f"Validation dataset size: {len(val_dataset)}")
print(f"Train X shape: {train_X_data.shape}, Train y shape: {train_y_labels.shape}")
print(f"Validation X shape: {val_X_data.shape}, Validation y shape: {val_y_labels.shape}")

# 클래스와 정수 매핑 정보 출력
print("Class-to-Index Mapping:")
for class_name, idx in class_to_idx.items():
    print(f"Class '{class_name}' is mapped to index {idx}")



Train dataset size: 2918
Validation dataset size: 596
Train X shape: (2918, 96, 17, 2), Train y shape: (2918,)
Validation X shape: (596, 96, 17, 2), Validation y shape: (596,)
Class-to-Index Mapping:
Class 'lying' is mapped to index 0
Class 'running' is mapped to index 1
Class 'sitting' is mapped to index 2
Class 'walking' is mapped to index 3


In [26]:
class LSTMPoseClassifier(nn.Module):
    def __init__(self, input_dim, hidden_dim, output_dim, num_layers=2, dropout=0.5):
        """
        LSTM 모델 초기화
        Args:
            input_dim (int): 입력 특징 차원 (17 * 2 = 34)
            hidden_dim (int): LSTM 은닉 상태 차원
            output_dim (int): 클래스 수
            num_layers (int): LSTM 레이어 수
            dropout (float): 드롭아웃 비율
        """
        super(LSTMPoseClassifier, self).__init__()
        self.lstm = nn.LSTM(input_dim, hidden_dim, num_layers, batch_first=True, dropout=dropout)
        self.fc = nn.Linear(hidden_dim, output_dim)  # 최종 분류 레이어

    def forward(self, x):
        """
        모델 순전파 정의
        Args:
            x (torch.Tensor): 입력 데이터 (batch_size, seq_length, input_dim)
        Returns:
            torch.Tensor: 클래스별 로짓 (batch_size, output_dim)
        """
        _, (hidden, _) = self.lstm(x)  # LSTM 출력
        hidden = hidden[-1]  # 마지막 LSTM 레이어의 출력
        output = self.fc(hidden)  # 최종 출력
        return output


In [27]:
# 하이퍼파라미터 설정
input_dim = 17 * 2  # 랜드마크 좌표 (x, y)
hidden_dim = 128  # LSTM 은닉 상태 차원
output_dim = len(class_names)  # 클래스 수
num_layers = 2  # LSTM 레이어 수
dropout = 0.5  # 드롭아웃 비율
learning_rate = 0.001  # 학습률
num_epochs = 200  # 에포크 수

# 모델 초기화
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = LSTMPoseClassifier(input_dim, hidden_dim, output_dim, num_layers, dropout).to(device)

# 손실 함수와 옵티마이저 정의
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)


In [28]:
def train_model(model, train_loader, val_loader, criterion, optimizer, num_epochs):
    for epoch in range(num_epochs):
        model.train()
        total_loss = 0
        correct = 0

        for X_batch, y_batch in train_loader:
            # 데이터 변환
            X_batch = X_batch.view(X_batch.size(0), X_batch.size(1), -1).to(device)
            y_batch = y_batch.to(device)

            # 순전파
            outputs = model(X_batch)
            loss = criterion(outputs, y_batch)
            total_loss += loss.item()

            # 역전파 및 가중치 업데이트
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()

            # 정확도 계산
            _, predicted = torch.max(outputs, 1)
            correct += (predicted == y_batch).sum().item()

        # 검증
        val_loss, val_accuracy = validate_model(model, val_loader, criterion)

        # 에포크 결과 출력
        print(f"Epoch [{epoch + 1}/{num_epochs}] - "
              f"Train Loss: {total_loss / len(train_loader):.4f}, "
              f"Train Accuracy: {correct / len(train_loader.dataset):.4f}, "
              f"Val Loss: {val_loss:.4f}, Val Accuracy: {val_accuracy:.4f}")


def validate_model(model, val_loader, criterion):
    model.eval()
    total_loss = 0
    correct = 0

    with torch.no_grad():
        for X_batch, y_batch in val_loader:
            # 데이터 변환
            X_batch = X_batch.view(X_batch.size(0), X_batch.size(1), -1).to(device)
            y_batch = y_batch.to(device)

            outputs = model(X_batch)
            loss = criterion(outputs, y_batch)
            total_loss += loss.item()

            _, predicted = torch.max(outputs, 1)
            correct += (predicted == y_batch).sum().item()

    return total_loss / len(val_loader), correct / len(val_loader.dataset)


In [29]:
# 모델 학습
train_model(model, train_loader, val_loader, criterion, optimizer, num_epochs)


Epoch [1/200] - Train Loss: 1.1763, Train Accuracy: 0.4184, Val Loss: 1.3682, Val Accuracy: 0.2248
Epoch [2/200] - Train Loss: 1.0535, Train Accuracy: 0.4887, Val Loss: 1.1281, Val Accuracy: 0.3826
Epoch [3/200] - Train Loss: 1.0292, Train Accuracy: 0.5007, Val Loss: 1.0330, Val Accuracy: 0.4765
Epoch [4/200] - Train Loss: 1.0329, Train Accuracy: 0.4818, Val Loss: 1.5520, Val Accuracy: 0.1946
Epoch [5/200] - Train Loss: 0.9811, Train Accuracy: 0.5027, Val Loss: 1.3890, Val Accuracy: 0.4547
Epoch [6/200] - Train Loss: 0.9665, Train Accuracy: 0.5284, Val Loss: 1.4616, Val Accuracy: 0.4010
Epoch [7/200] - Train Loss: 0.9657, Train Accuracy: 0.5805, Val Loss: 0.9190, Val Accuracy: 0.5654
Epoch [8/200] - Train Loss: 0.8356, Train Accuracy: 0.6374, Val Loss: 1.1225, Val Accuracy: 0.4748
Epoch [9/200] - Train Loss: 0.8046, Train Accuracy: 0.6432, Val Loss: 1.2055, Val Accuracy: 0.4060
Epoch [10/200] - Train Loss: 0.7177, Train Accuracy: 0.6741, Val Loss: 0.6805, Val Accuracy: 0.7047
Epoch [11

In [30]:
torch.save(model.state_dict(), "lstm_pose_classifier2.0.pth")
print("Model saved as lstm_pose_classifier2.0.pth")


Model saved as lstm_pose_classifier2.0.pth
